In [ ]:
# !pip install faiss-cpu
# !pip uninstall numpy
!pip install numpy



In [ ]:
!pip install --upgrade pandas


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 91.2/91.2 kB 4.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.4/12.4 MB 97.5 MB/s eta 0:00:00
  Attempting uninstall: pandas
    Found existing installation: pandas 2.2.2
    Uninstalling pandas-2.2.2:
      Successfully uninstalled pandas-2.2.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
google-colab 1.0.0 requires pandas==2.2.2, but you have pandas 2.3.1 which is incompatible.
dask-cudf-cu12 25.6.0 requires pandas<2.2.4dev0,>=2.0, but you have pandas 2.3.1 which is incompatible.
cudf-cu12 25.6.0 requires pandas<2.2.4dev0,>=2.0, but you have pandas 2.3.1 which is incompatible.


In [ ]:
# !pip install tqdm
# !pip install scikit-learn
# !pip install openpyxl
!pip install lark



In [ ]:
!pip install langchain-community
!pip install langchain-huggingface


In [ ]:
!pip install sentence-transformers


In [ ]:
# !pip install chromadb
!pip install langchain-openai
!pip install langchain-chroma


In [ ]:
import pandas as pd
df = pd.read_csv('new.csv')
print(df.columns.tolist())

['r_id', 'r_name', 'city', 'r_rating', 'r_rating_count', 'avg_price_per_person', 'cuisine', 'f_id', 'avg_price_per_item', 'f_name', 'veg_or_non_veg', 'f_rating', 'f_rating_count', 'label', 'f_price', 'RatingMomentum', 'PopularityScore', 'ItemPremium', 'FoodRatingEfficiency', 'ItemPopularity', 'ValueIndex', 'PremiumLabel', 'HealthLabel', 'NewOrSeasonal', 'PromoIneligible', 'MenuSize', 'AvgItemRatingPerRestaurant', 'PriceRange', 'RatingGap', 'CuisineCityCount', 'cuisine_1', 'cuisine_2']


In [ ]:

import gc
import os
import json
import pandas as pd
import chromadb
from langchain_chroma import Chroma
from langchain_huggingface import HuggingFaceEmbeddings
from langchain_core.documents import Document
from tqdm import tqdm
import os
from langchain_openai import ChatOpenAI

In [ ]:
os.environ["OPENAI_API_KEY"] = "Enter_your_key"
os.environ["HF_TOKEN"] = "Enter_your_key"

In [ ]:
# !pip install chromadb
import chromadb
import pandas as pd
import numpy as np
import warnings
import gc
import os
import sys
from typing import Dict, List, Any, Optional
import logging
from tqdm import tqdm
import psutil

In [ ]:
import os
import asyncio
from concurrent.futures import ThreadPoolExecutor
from langchain_huggingface import HuggingFaceEndpoint
from langchain_chroma import Chroma
from langchain_community.query_constructors.chroma import ChromaTranslator
from langchain.chains.query_constructor.base import (
    StructuredQueryOutputParser,
    get_query_constructor_prompt,
)
import chromadb

In [ ]:
# Phase 2 - Block 1: Import Libraries (Memory Optimized)


# Setup logging
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')
logger = logging.getLogger(__name__)
warnings.filterwarnings('ignore')

# Memory monitoring function
def check_memory():
    memory = psutil.virtual_memory()
    print(f"💾 Memory: {memory.available / (1024**3):.1f} GB available ({memory.percent:.1f}% used)")
    return memory.percent < 85

print("✅ Libraries imported successfully!")
print("📋 Phase 2: Memory-Optimized Embeddings & Vector Store Setup")
check_memory()


✅ Libraries imported successfully!
📋 Phase 2: Memory-Optimized Embeddings & Vector Store Setup
💾 Memory: 10.8 GB available (14.9% used)


True

In [ ]:
# Phase 2 - Block 2: Memory-Efficient Data Loading

def optimize_dtypes(df):
    """Optimize data types to reduce memory usage"""
    original_memory = df.memory_usage(deep=True).sum()

    # Optimize numeric columns
    for col in df.select_dtypes(include=['int64']).columns:
        col_min, col_max = df[col].min(), df[col].max()
        if col_min >= 0:  # Unsigned integers
            if col_max <= 255:
                df[col] = df[col].astype(np.uint8)
            elif col_max <= 65535:
                df[col] = df[col].astype(np.uint16)
            else:
                df[col] = df[col].astype(np.uint32)
        else:  # Signed integers
            if col_min >= -128 and col_max <= 127:
                df[col] = df[col].astype(np.int8)
            elif col_min >= -32768 and col_max <= 32767:
                df[col] = df[col].astype(np.int16)
            else:
                df[col] = df[col].astype(np.int32)

    # Optimize float columns
    for col in df.select_dtypes(include=['float64']).columns:
        df[col] = pd.to_numeric(df[col], downcast='float')

    # Convert low-cardinality object columns to category
    for col in df.select_dtypes(include=['object']).columns:
        if col in df.columns:
            unique_ratio = df[col].nunique() / len(df)
            if unique_ratio < 0.5:  # Less than 50% unique values
                df[col] = df[col].astype('category')

    new_memory = df.memory_usage(deep=True).sum()
    print(f"💾 Memory optimized: {original_memory/1024**2:.1f}MB → {new_memory/1024**2:.1f}MB "
          f"({(1-new_memory/original_memory)*100:.1f}% reduction)")

    return df

def validate_and_clean_data(df):
    """Validate and clean the restaurant data"""

    # Required columns based on your data structure
    required_cols = ['r_id', 'r_name', 'f_id', 'f_name', 'cuisine', 'veg_or_non_veg',
                     'avg_price_per_item', 'f_rating', 'city']

    # Check for missing required columns
    missing_cols = [col for col in required_cols if col not in df.columns]
    if missing_cols:
        logger.warning(f"Missing columns: {missing_cols}")

    optional_cols = ['cuisine_1', 'cuisine_2']

    # Clean and validate data
    df = df.copy()

    # Handle new cuisine columns if they exist
    if 'cuisine_1' in df.columns:
        df['cuisine_1'] = df['cuisine_1'].fillna('unknown').astype(str)

    if 'cuisine_2' in df.columns:
        df['cuisine_2'] = df['cuisine_2'].fillna('').astype(str)

    # Clean and validate data
    df = df.copy()

    # Fix ratings
    df['f_rating'] = pd.to_numeric(df['f_rating'], errors='coerce').fillna(3.0).clip(0, 5)

    # Fix prices
    df['avg_price_per_item'] = pd.to_numeric(df['avg_price_per_item'], errors='coerce')
    df['avg_price_per_item'] = df['avg_price_per_item'].fillna(df['avg_price_per_item'].median()).clip(1, None)

    # Fix veg/non-veg
    valid_diet = ['Veg', 'Non-veg','vegan']
    df.loc[~df['veg_or_non_veg'].isin(valid_diet), 'veg_or_non_veg'] = 'Non-veg'

    # Fill text fields
    text_cols = ['f_name', 'r_name', 'city', 'cuisine', 'label']
    for col in text_cols:
        if col in df.columns:
            df[col] = df[col].fillna('unknown').astype(str)

    logger.info(f"✅ Data validated: {len(df)} rows")
    return df

def load_restaurant_data(file_path, max_rows=None):
    """Load restaurant data with memory optimization"""
    logger.info(f"🔄 Loading data from: {file_path}")

    if not os.path.exists(file_path):
        raise FileNotFoundError(f"File not found: {file_path}")

    try:
        # Determine file type and load accordingly
        if file_path.endswith('.xlsx'):
            df = pd.read_excel(file_path, nrows=max_rows)
        else:
            # For large CSV files, use chunked reading
            if max_rows and max_rows <= 100000:
                df = pd.read_csv(file_path, nrows=max_rows)
            else:
                # Load in chunks for memory efficiency
                chunk_size = 50000
                chunks = []
                total_rows = 0

                for chunk in tqdm(pd.read_csv(file_path, chunksize=chunk_size),
                                desc="Loading chunks"):
                    if max_rows and total_rows >= max_rows:
                        break

                    chunk = validate_and_clean_data(chunk)
                    chunk = optimize_dtypes(chunk)
                    chunks.append(chunk)
                    total_rows += len(chunk)

                    # Memory check
                    if not check_memory():
                        logger.warning("⚠️ Memory getting low, stopping data loading")
                        break

                df = pd.concat(chunks, ignore_index=True)
                del chunks
                gc.collect()

        # Validate and optimize the final dataframe
        df = validate_and_clean_data(df)
        df = optimize_dtypes(df)

        # Reset index
        df = df.reset_index(drop=True)

        logger.info(f"✅ Data loaded successfully: {len(df):,} rows, {len(df.columns)} columns")
        print(f"📊 Memory usage: {df.memory_usage(deep=True).sum() / 1024**2:.1f} MB")

        return df

    except Exception as e:
        logger.error(f"❌ Error loading data: {e}")
        raise

print("🔧 Memory-efficient data loading functions defined")


🔧 Memory-efficient data loading functions defined


In [ ]:
# Phase 2 - Block 3: Complete Feature Engineering Functions (Memory Efficient)

def normalize_text_efficient(df):
    """Memory-efficient text normalization - COMPLETE normalization here"""
    df = df.copy()

    text_columns = ['cuisine', 'cuisine_1', 'cuisine_2', 'f_name', 'r_name', 'city', 'label', 'veg_or_non_veg']

    # Normalize ALL text columns that will be used in JSON
    for col in text_columns:
        if col in df.columns:
            df[col] = (df[col]
                      .astype(str)
                      .str.lower()
                      .str.strip()
                      .str.replace(r'[^\w\s,]', '', regex=True)
                      .str.replace(r'\s+', ' ', regex=True))

    logger.info("✅ Text normalization completed")
    return df

def create_price_tiers_efficient(df):
    """Create price tiers based on data distribution"""
    df = df.copy()

    # Calculate dynamic percentiles
    price_col = 'avg_price_per_item'
    if price_col in df.columns:
        percentiles = df[price_col].quantile([0.25, 0.5, 0.75]).values

        # Create bins
        bins = [0, percentiles[0], percentiles[1], percentiles[2], float('inf')]
        labels = ['budget', 'affordable', 'premium', 'luxury']

        df['price_tier'] = pd.cut(df[price_col], bins=bins, labels=labels, include_lowest=True)
        df['price_tier'] = df['price_tier'].astype(str).fillna('affordable')

        tier_dist = df['price_tier'].value_counts()
        logger.info(f"✅ Price tiers created: {tier_dist.to_dict()}")

    return df

def create_structured_json_data(df):
    """Create structured JSON data for better semantic understanding - Memory Efficient"""
    df = df.copy()

    def determine_popularity_level(row):
        """Extract popularity level from PopularityScore (your existing logic)"""
        if 'PopularityScore' in row and pd.notna(row['PopularityScore']):
            pop_score = float(row['PopularityScore'])
            if pop_score > 500:
                return 'very_popular'
            elif pop_score > 300:
                return 'popular'
            else:
                return 'emerging'
        return 'emerging'

    def determine_momentum_level(row):
        """Extract momentum level from RatingMomentum (your existing logic)"""
        if 'RatingMomentum' in row and pd.notna(row['RatingMomentum']):
            momentum = float(row['RatingMomentum'])
            if momentum > 8:
                return 'high_momentum'
            elif momentum > 5:
                return 'medium_momentum'
            else:
                return 'low_momentum'
        return 'low_momentum'

    def row_to_json_structure(row):
        """Convert row to structured JSON format (matching your component order)"""
        primary_cuisine = str(row.get('cuisine', '')).strip()

        # Enhanced cuisine handling with splits
        cuisine_1 = str(row.get('cuisine_1', '')).strip()
        cuisine_2 = str(row.get('cuisine_2', '')).strip()

        # Create comprehensive cuisine description
        cuisine_description = primary_cuisine
        if cuisine_1 and cuisine_1 != 'unknown':
            cuisine_description = cuisine_1
            if cuisine_2 and cuisine_2 != '':
                cuisine_description += f", {cuisine_2}"

        json_structure = {  # Enhanced with split data
             # NEW: Secondary cuisine
            "food": str(row.get('f_name', '')).strip(),
            "dietary": str(row.get('veg_or_non_veg', '')).strip(),
            "price_tier": str(row.get('price_tier', '')).strip(),
            "label": str(row.get('label', '')).strip(),
            "location": str(row.get('city', '')).strip(),
            "restaurant": str(row.get('r_name', '')).strip(),
            "popularity": determine_popularity_level(row),
            "cuisine_1": str(row.get('cuisine_1', '')).strip(),    # NEW: Primary cuisine
            "cuisine_2": str(row.get('cuisine_2', '')).strip(),
            "f_id": str(row.get('f_id', '')).strip(),
            "r_id": str(row.get('r_id', '')).strip(),
            "f_price": int(row.get('f_price', 0)) if pd.notna(row.get('f_price')) else 0,
            "f_rating": float(row.get('f_rating', 0)) if pd.notna(row.get('f_rating')) else 0.0,
            "r_rating": float(row.get('r_rating', 0)) if pd.notna(row.get('r_rating')) else 0.0
        }
        return json_structure


    # Function to create JSON string for embedding
    def create_json_string_for_embedding(json_struct):
        """Convert JSON to formatted string for better embedding semantics"""

        if json_struct['cuisine_1'] and json_struct['cuisine_1'] != 'unknown':
            if json_struct['cuisine_2'] and json_struct['cuisine_2'] != '':
                cuisine_desc = f"{json_struct['cuisine_1']} and {json_struct['cuisine_2']} cuisine"
            else:
                cuisine_desc = f"{json_struct['cuisine_1']} cuisine"
        else:
            cuisine_desc = "mixed cuisine"

        return f"""food name is '{json_struct['food']}', comes under '{cuisine_desc}' dish, it's dietary: {json_struct['dietary']} """

    # Memory-efficient batch processing (maintaining your approach)
    batch_size = 10000
    json_structures = []
    json_strings = []

    for i in tqdm(range(0, len(df), batch_size), desc="Creating JSON structures"):
        batch = df.iloc[i:i+batch_size]

        # Process batch
        batch_json_structs = []
        batch_json_strings = []

        for idx, row in batch.iterrows():
            json_struct = row_to_json_structure(row)
            json_string = create_json_string_for_embedding(json_struct)

            # Filter valid components (your existing logic)
            if json_string and json_string.strip():
                batch_json_structs.append(json_struct)
                batch_json_strings.append(json_string)
            else:
                # Fallback for empty entries
                batch_json_structs.append(json_struct)
                batch_json_strings.append(f"food: {json_struct['food']}")

        json_structures.extend(batch_json_structs)
        json_strings.extend(batch_json_strings)

        # Memory cleanup (maintaining your pattern)
        if i % 50000 == 0 and i > 0:
            gc.collect()
            if not check_memory():
                logger.warning("⚠️ Memory limit reached, stopping JSON creation")
                break

    # Add to dataframe
    df['json_metadata'] = json_structures
    df['json_string_for_embedding'] = json_strings

    # Text statistics (similar to your existing logging)
    text_lengths = pd.Series(json_strings).str.len()
    logger.info(f"✅ JSON structures created - Count: {len(json_strings)}, Mean length: {text_lengths.mean():.1f}, Max: {text_lengths.max()}")

    return df

def create_metadata_schema():
    """Define metadata schema for LangChain self-querying"""
    from langchain.chains.query_constructor.schema import AttributeInfo

    metadata_field_info = [
        AttributeInfo(
            name="food",
            description='''Name of the food item (e.g., burger, pizza, pasta)''',
            type="string"
        ),
        AttributeInfo(
            name="cuisine_1",
            description='''Type of cuisine
            'beverages', 'sweets', 'fast food', 'italian-american', 'continental',
 'north indian', 'snacks', 'indian', 'juices', 'tandoor', 'punjabi', 'mughlai',
 'pizzas', 'chinese', 'ice cream', 'chaat', 'bakery', 'american', 'european',
 'biryani', 'south indian', 'desserts', 'street food', 'nepalese', 'paan',
 'healthy food', 'bengali', 'thalis', 'waffle', 'arabian', 'combo', 'tibetan',
 'burgers', 'bihari', 'italian', 'salads', 'kebabs', 'asian', 'thai',
 'north eastern', 'cafe', 'pan-asian', 'lebanese', 'maharashtrian', 'mexican',
 'pastas', 'rajasthani', 'gujarati', 'seafood', 'japanese', 'sushi',
 'middle eastern', 'french', 'hyderabadi', 'grill',
 'svanidhi street food vendor', 'afghani', 'oriental', 'home food', 'barbecue',
 'korean', 'kerala', 'andhra', 'british', 'oriya', 'portuguese', 'lucknowi',
 'mangalorean', 'chettinad', 'mediterranean', 'naga', 'turkish', 'assamese',
 'steakhouse', 'coastal', 'tex-mex'
 ''',
            type="string"
        ),
        AttributeInfo(
            name="cuisine_2",
            description='''Type of cuisine
            'pizzas', 'bakery', 'indian', 'fast food', 'chaat', 'beverages', 'desserts',
 'chinese', 'north indian', 'tandoor', 'american', 'thalis', 'snacks',
 'south indian', 'italian', 'street food', 'kebabs', 'biryani', 'salads',
 'pastas', 'continental', 'bengali', 'burgers', 'ice cream', 'tibetan', 'thai',
 'hyderabadi', 'sweets', 'lebanese', 'nepalese', 'mughlai', 'lucknowi',
 'healthy food', 'afghani', 'asian', 'combo', 'seafood', 'waffle',
 'italian-american', 'punjabi', 'arabian', 'barbecue', 'mexican',
 'ice cream cakes', 'gujarati', 'juices', 'jain', 'pan-asian', 'rajasthani',
 'mediterranean', 'burmese', 'oriental', 'maharashtrian', 'kerala', 'home food',
 'indonesian', 'middle eastern', 'grill', 'japanese', 'paan',
 'biryani - shivaji military hotel', 'greek', 'cafe',
 'use code jumbo30 to avail', 'chettinad', 'coastal', 'andhra', 'turkish',
 'african', 'tex-mex', 'oriya', 'british', 'mangalorean', 'bihari', 'keto',
 'european', 'malaysian', 'north eastern'
 ''',
            type="string"
        ),
        AttributeInfo(
            name="dietary",
            description='''Dietary preference: "veg" or "nonveg" or "vegan" ''',
            type="string"
        ),
        AttributeInfo(
            name="price_tier",
            description='''Price tier: within the budget use "budget", not under  budget use "affordable",and other are  "premium", or "luxury" ''',
            type="string"
        ),
        AttributeInfo(
            name="popularity",
            description='''Popularity level: if its recently getting famous use "emerging",already popular use "popular", or "very_popular" accordingly''',
            type="string"
        ),
        AttributeInfo(
            name="label",
            description='''Special labels like
            'bestseller', 'must try',
 "chef's special", 'new', 'seasonal', 'spicy', 'fodmap friendly',
 'eggless available', 'gluten free', 'dairy free'
 ''',
            type="string"
        ),
        AttributeInfo(
            name="location",
            description='''City or location where the restaurant and food is available
            'abohar', 'adilabad', 'adityapur', 'adoni', 'agartala', 'agra',
 'vastrapur,ahmedabad', 'gota,ahmedabad', 'paldi & ambawadi,ahmedabad',
 'ghatlodia,ahmedabad', 'bopal,ahmedabad', 'gandhinagar,ahmedabad',
 'laldarwaja,ahmedabad', 'naranpura,ahmedabad', 'navrangpura,ahmedabad',
 'science city,ahmedabad', 'maninagar,ahmedabad', 'chandkheda,ahmedabad',
 'ahmednagar', 'aizawl', 'ajmer', 'akola', 'alappuzha', 'aligarh', 'alipurduar',
 'allahabad', 'alwar', 'ambala', 'ambikapur', 'ambur', 'amravati', 'amreli',
 'amritsar', 'anand', 'anantapur', 'ankleshwar', 'arakkonam', 'arambagh',
 'arrah', 'aruppukottai', 'asansol', 'aurangabad', 'aurangabad_bihar',
 'azamgarh', 'baddi', 'bagalkot', 'bagdogra', 'bahadurgarh', 'bahraich',
 'balaghat', 'balangir', 'balasore', 'ballari', 'balrampur', 'balurghat',
 'banda', 'yeshwanthpur,bangalore', 'geddalahalli,bangalore',
 'koramangala,bangalore', 'jp nagar,bangalore', 'mahadevpura,bangalore',
 'hsr,bangalore'
            ''',
            type="string"
        ),
        AttributeInfo(
            name="restaurant",
            description="Name of the restaurant serving the food",
            type="string"
        ),
        AttributeInfo(
            name="f_id",
            description="Unique identifier for the food item",
            type="string"
        ),
        AttributeInfo(
            name="r_id",
            description="Unique identifier for the restaurant",
            type="string"
        ),
        AttributeInfo(
            name="f_price",
            description='''Price of the food item in INR, used for tiering''',
            type="integer"
        ),
        AttributeInfo(
            name="f_rating",
            description='''Rating of the food item out of 5''',
            type="float"
        ),
        AttributeInfo(
            name="r_rating",
            description='''Rating of the restaurant out of 5''',
            type="float"
        ),
    ]

    document_content_description = "Food items with detailed information about cuisine, dietary preferences, popularity, and availability"

    return metadata_field_info, document_content_description

print("🔧 All feature engineering functions defined (Memory Efficient)")
print("   - normalize_text_efficient")
print("   - create_price_tiers_efficient")
print("   - create_structured_json_data")
print("   - create_metadata_schema")


🔧 All feature engineering functions defined (Memory Efficient)
   - normalize_text_efficient
   - create_price_tiers_efficient
   - create_structured_json_data
   - create_metadata_schema


In [ ]:
# Phase 2 - Block 4: Load and Process Data with JSON Structure

# File path configuration
file_path = "../1mdata.csv"  # Update this to your 1M dataset path
sample_file = "new.csv"  # Your existing sample data file


# Fallback to sample data if main file doesn't exist or failed to load
if not os.path.exists(file_path):
    print(f"📄 Loading sample data from {sample_file}...")

    df_restaurant_raw = pd.read_csv(sample_file)
    # df_restaurant_raw = df_restaurant_raw.head(10000)  # Limit to 10K for testing


# Initial data validation
print(f"\n📊 Raw Data Overview:")
print(f" Shape: {df_restaurant_raw.shape}")
print(f" Memory: {df_restaurant_raw.memory_usage(deep=True).sum() / 1024**2:.1f} MB")
print(f" Columns: {list(df_restaurant_raw.columns)}")

# Step 1: Apply text normalization (from Block 3)
print("\n🔄 Step 1: Applying text normalization...")
df_restaurant_processed = normalize_text_efficient(df_restaurant_raw)
gc.collect()  # Memory cleanup

# Step 2: Create price tiers (from Block 3)
print("🔄 Step 2: Creating price tiers...")
df_restaurant_processed = create_price_tiers_efficient(df_restaurant_processed)
gc.collect()  # Memory cleanup

# Step 3: Create JSON structures (NEW - from Block 3)
print("🔄 Step 3: Creating JSON structures for semantic understanding...")
df_restaurant_processed = create_structured_json_data(df_restaurant_processed)
gc.collect()  # Memory cleanup

# Step 4: Setup metadata schema for self-querying (from Block 3)
print("🔄 Step 4: Setting up metadata schema for self-querying...")
metadata_field_info, document_content_description = create_metadata_schema()

# Data validation and overview
print(f"\n📊 Processed Data Overview:")
print(f" Shape: {df_restaurant_processed.shape}")
print(f" Memory: {df_restaurant_processed.memory_usage(deep=True).sum() / 1024**2:.1f} MB")
print(f" Processing completed successfully: {len(df_restaurant_processed):,} records")



📄 Loading sample data from new.csv...

📊 Raw Data Overview:
 Shape: (1063888, 32)
 Memory: 806.2 MB
 Columns: ['r_id', 'r_name', 'city', 'r_rating', 'r_rating_count', 'avg_price_per_person', 'cuisine', 'f_id', 'avg_price_per_item', 'f_name', 'veg_or_non_veg', 'f_rating', 'f_rating_count', 'label', 'f_price', 'RatingMomentum', 'PopularityScore', 'ItemPremium', 'FoodRatingEfficiency', 'ItemPopularity', 'ValueIndex', 'PremiumLabel', 'HealthLabel', 'NewOrSeasonal', 'PromoIneligible', 'MenuSize', 'AvgItemRatingPerRestaurant', 'PriceRange', 'RatingGap', 'CuisineCityCount', 'cuisine_1', 'cuisine_2']

🔄 Step 1: Applying text normalization...
🔄 Step 2: Creating price tiers...
🔄 Step 3: Creating JSON structures for semantic understanding...


Creating JSON structures:   6%|▌         | 6/107 [00:04<01:24,  1.19it/s]

💾 Memory: 8.8 GB available (30.8% used)


Creating JSON structures:  10%|█         | 11/107 [00:09<01:44,  1.09s/it]

💾 Memory: 8.8 GB available (30.8% used)


...

💾 Memory: 8.2 GB available (35.5% used)


Creating JSON structures:  99%|█████████▉| 106/107 [01:35<00:00,  1.02it/s]

💾 Memory: 8.1 GB available (35.8% used)


Creating JSON structures: 100%|██████████| 107/107 [01:36<00:00,  1.11it/s]


🔄 Step 4: Setting up metadata schema for self-querying...

📊 Processed Data Overview:
 Shape: (1063888, 35)
 Memory: 1518.0 MB
 Processing completed successfully: 1,063,888 records


In [ ]:
df_restaurant_processed.to_csv('df_restaurant_processed3.csv', index=False)

In [ ]:
import torch
import gc

def clear_gpu_memory():
    """Clear GPU memory before starting embedding process"""
    if torch.cuda.is_available():
        # Clear PyTorch cache
        torch.cuda.empty_cache()

        # Force garbage collection
        gc.collect()

        # Print GPU memory status
        print(f"🔥 GPU memory cleared")
        print(f"📊 GPU memory allocated: {torch.cuda.memory_allocated()/1024**3:.2f} GB")
        print(f"📊 GPU memory cached: {torch.cuda.memory_reserved()/1024**3:.2f} GB")

        return True
    else:
        print("❌ CUDA not available")
        return False

# Call before starting your embedding process
clear_gpu_memory()


🔥 GPU memory cleared
📊 GPU memory allocated: 0.09 GB
📊 GPU memory cached: 0.10 GB


True

In [ ]:
df_restaurant_raw

r_id                 r_name           city  r_rating  \
0        567335.0         AB FOODS POINT         Abohar       1.9   
1        567335.0         AB FOODS POINT         Abohar       2.0   
2        567335.0         AB FOODS POINT         Abohar       2.7   
3        567335.0         AB FOODS POINT         Abohar       2.0   
4        567335.0         AB FOODS POINT         Abohar       1.3   
...           ...                    ...            ...       ...   
1063883   96525.0  IceBreakers Ice Cream  HSR,Bangalore       3.4   
1063884   96525.0  IceBreakers Ice Cream  HSR,Bangalore       3.4   
1063885   96525.0  IceBreakers Ice Cream  HSR,Bangalore       3.4   
1063886   96525.0  IceBreakers Ice Cream  HSR,Bangalore       3.4   
1063887   96525.0  IceBreakers Ice Cream  HSR,Bangalore       3.4   

         r_rating_count  avg_price_per_person             cuisine       f_id  \
0                    20                 200.0    Beverages,Pizzas        fd0   
1                    15                 200.0    Beverages,Pizzas   fd669322   
2                    18                 200.0    Beverages,Pizzas        fd1   
3                    12                 200.0    Beverages,Pizzas        fd2   
4                    10                 200.0    Beverages,Pizzas        fd3   
...                 ...                   ...                 ...        ...   
1063883              34                 200.0  Ice Cream,Desserts  fd1048555   
1063884              48                 200.0  Ice Cream,Desserts  fd1048556   
1063885              39                 200.0  Ice Cream,Desserts  fd1048558   
1063886              23                 200.0  Ice Cream,Desserts  fd1048561   
1063887              38                 200.0  Ice Cream,Desserts  fd1048562   

         avg_price_per_item                  f_name  ... HealthLabel  \
0                      40.0       Aloo Tikki Burger  ...           0   
1                      40.0       Aloo Tikki Burger  ...           0   
2                      50.0       Veg Creamy Burger  ...           0   
3                      65.0     Cheese Burst Burger  ...           0   
4                      80.0    Paneer Creamy Burger  ...           0   
...                     ...                     ...  ...         ...   
1063883               300.0    Sizzlers De- Verdure  ...           0   
1063884               300.0         Veg Bbq Sizzler  ...           0   
1063885               350.0    Veg Sizzling Italian  ...           0   
1063886               200.0  Veg Overload  Sandwich  ...           0   
1063887               270.0    Aglio Riso Rice Bowl  ...           0   

         NewOrSeasonal  PromoIneligible MenuSize  AvgItemRatingPerRestaurant  \
0                    0                0      131                    3.845802   
1                    0                0      131                    3.845802   
2                    0                0      131                    3.845802   
3                    0                1      131                    3.845802   
4                    0                1      131                    3.845802   
...                ...              ...      ...                         ...   
1063883              0                0       57                    3.819298   
1063884              0                0       57                    3.819298   
1063885              0                0       57                    3.819298   
1063886              0                0       57                    3.819298   
1063887              0                0       57                    3.819298   

         PriceRange  RatingGap  CuisineCityCount  cuisine_1  cuisine_2  
0           1595.16        2.1                 3  Beverages     Pizzas  
1           1595.16        1.9                 3  Beverages     Pizzas  
2           1595.16        0.7                 3  Beverages     Pizzas  
3           1595.16        1.8                 3  Beverages     Pizzas  
4           1595.16        2.7  

In [ ]:
df_restaurant_processed


r_id                 r_name           city  r_rating  \
0        567335.0         ab foods point         abohar       1.9   
1        567335.0         ab foods point         abohar       2.0   
2        567335.0         ab foods point         abohar       2.7   
3        567335.0         ab foods point         abohar       2.0   
4        567335.0         ab foods point         abohar       1.3   
...           ...                    ...            ...       ...   
1063883   96525.0  icebreakers ice cream  hsr,bangalore       3.4   
1063884   96525.0  icebreakers ice cream  hsr,bangalore       3.4   
1063885   96525.0  icebreakers ice cream  hsr,bangalore       3.4   
1063886   96525.0  icebreakers ice cream  hsr,bangalore       3.4   
1063887   96525.0  icebreakers ice cream  hsr,bangalore       3.4   

         r_rating_count  avg_price_per_person             cuisine       f_id  \
0                    20                 200.0    beverages,pizzas        fd0   
1                    15                 200.0    beverages,pizzas   fd669322   
2                    18                 200.0    beverages,pizzas        fd1   
3                    12                 200.0    beverages,pizzas        fd2   
4                    10                 200.0    beverages,pizzas        fd3   
...                 ...                   ...                 ...        ...   
1063883              34                 200.0  ice cream,desserts  fd1048555   
1063884              48                 200.0  ice cream,desserts  fd1048556   
1063885              39                 200.0  ice cream,desserts  fd1048558   
1063886              23                 200.0  ice cream,desserts  fd1048561   
1063887              38                 200.0  ice cream,desserts  fd1048562   

         avg_price_per_item                 f_name  ... MenuSize  \
0                      40.0      aloo tikki burger  ...      131   
1                      40.0      aloo tikki burger  ...      131   
2                      50.0      veg creamy burger  ...      131   
3                      65.0    cheese burst burger  ...      131   
4                      80.0   paneer creamy burger  ...      131   
...                     ...                    ...  ...      ...   
1063883               300.0    sizzlers de verdure  ...       57   
1063884               300.0        veg bbq sizzler  ...       57   
1063885               350.0   veg sizzling italian  ...       57   
1063886               200.0  veg overload sandwich  ...       57   
1063887               270.0   aglio riso rice bowl  ...       57   

         AvgItemRatingPerRestaurant  PriceRange RatingGap  CuisineCityCount  \
0                          3.845802     1595.16       2.1                 3   
1                          3.845802     1595.16       1.9                 3   
2                          3.845802     1595.16       0.7                 3   
3                          3.845802     1595.16       1.8                 3   
4                          3.845802     1595.16       2.7                 3   
...                             ...         ...       ...               ...   
1063883                    3.819298     1133.60       0.3                13   
1063884                    3.819298     1133.60       0.9                13   
1063885                    3.819298     1133.60       0.3                13   
1063886                    3.819298     1133.60       0.6                13   
1063887                    3.819298     1133.60       0.1                13   

         cuisine_1  cuisine_2  price_tier  \
0        beverages     pizzas      budget   
1        beverages     pizzas      budget   
2        beverages     pizzas      budget   
3        beverages     pizzas      budget   
4        beverages     pizzas      budget   
...            ...        ...         ...   
1063883  ice cream   desserts      luxury   
1063884  ice cream   desserts      luxury   
1063885  ice cream   desserts      luxury   
1063886

In [ ]:
len(df_restaurant_processed)

1063888

In [ ]:
print(df_restaurant_processed["json_metadata"].iloc[0])

{'food': 'aloo tikki burger', 'dietary': 'veg', 'price_tier': 'budget', 'label': 'bestseller', 'location': 'abohar', 'restaurant': 'ab foods point', 'popularity': 'very_popular', 'cuisine_1': 'beverages', 'cuisine_2': 'pizzas', 'f_id': 'fd0', 'r_id': '567335.0', 'f_price': 299, 'f_rating': 4.0, 'r_rating': 1.9}


In [ ]:
import os
import gc
import psutil
import chromadb
from langchain.docstore.document import Document
from tqdm import tqdm
import torch


def setup_embeddings():
    available_memory_gb = psutil.virtual_memory().available / (1024**3)
    model_name = "sentence-transformers/all-MiniLM-L6-v2"


    embeddings = HuggingFaceEmbeddings(
        model_name=model_name,
        model_kwargs={"device": "cuda"},
        encode_kwargs={
            "batch_size" : 1536,  # tune to fill ~90% of your VRAM
            "normalize_embeddings": True
        }
    )

    return embeddings

# Setup embeddings
embeddings = setup_embeddings()

print("done")




done


In [ ]:


def check_memory():
    """Simple memory check function"""
    available_memory_gb = psutil.virtual_memory().available / (1024**3)
    return available_memory_gb > 1.0  # Return True if more than 1GB available

def create_documents_from_dataframe(df, batch_size=1000):
    required_columns = ['json_string_for_embedding', 'json_metadata']
    missing_columns = [col for col in required_columns if col not in df.columns]

    if missing_columns:
        raise KeyError(f"Missing columns: {missing_columns}")

    documents = []
    failed_docs = 0

    print(f"📝 Processing {len(df)} records into documents...")

    with tqdm(total=len(df), desc="Creating documents", unit="docs") as pbar:
        for i in range(0, len(df), batch_size):
            batch = df.iloc[i:i+batch_size]

            for idx, row in batch.iterrows():
                try:
                    # Validate required fields
                    if pd.isna(row['json_string_for_embedding']) or row['json_string_for_embedding'] == '':
                        failed_docs += 1
                        pbar.update(1)
                        continue

                    page_content = str(row['json_string_for_embedding'])

                    # Handle metadata safely
                    if pd.isna(row['json_metadata']):
                        metadata = {}
                    else:
                        raw_metadata = row['json_metadata']

                        # Type-safe metadata processing
                        raw_metadata = row['json_metadata']

                        # Type-safe metadata processing
                        metadata = {}
                        for key, value in raw_metadata.items():
                            if key == 'f_price':
                              metadata[key] = int(value)

                            elif key == 'f_rating' or key == 'r_rating':
                                # Handle f_rating as float (since ratings can be decimal)
                                try:
                                    metadata[key] = float(value) if value is not None else 0.0
                                except (ValueError, TypeError):
                                    metadata[key] = 0.0
                            else:
                            # String fields
                                metadata[key] = str(value) if value is not None else ""


                    # Convert metadata values to strings safely
                    processed_metadata = {}
                    for key, value in metadata.items():
                        try:
                            processed_metadata[str(key)] = str(value) if value is not None else ""
                        except:
                            processed_metadata[str(key)] = ""

                    doc = Document(
                        page_content=page_content,
                        metadata=metadata
                    )
                    documents.append(doc)

                except Exception as e:
                    failed_docs += 1
                    print(f"⚠️ Failed to process row {idx}: {str(e)}")

                pbar.update(1)

            # Memory management
            if i % (batch_size * 5) == 0 and i > 0:
                gc.collect()
                if not check_memory():
                    print(f"⚠️ Low memory detected, stopping document creation at {i} records")
                    break

    print(f"✅ Created {len(documents)} documents, failed: {failed_docs}")
    return documents

def create_multi_shard_chroma_store(df_restaurant_processed, embeddings, shard_size=250000):
    total_records = len(df_restaurant_processed)
    num_shards = max(1, (total_records + shard_size - 1) // shard_size)

    print(f"🚀 Processing {total_records:,} records into {num_shards} shards")
    print(f"📊 Shard size: {shard_size:,} records per shard")

    # Create directories
    base_dir = "./chroma_shards"
    data_dir = "./shard_data"
    os.makedirs(base_dir, exist_ok=True)
    os.makedirs(data_dir, exist_ok=True)

    shard_info_list = []
    successful_shards = 0
    failed_shards = 0

    with tqdm(total=num_shards, desc="Creating shards", unit="shard") as shard_pbar:
        for shard_id in range(num_shards):
            start_idx = shard_id * shard_size
            end_idx = min(start_idx + shard_size, total_records)
            shard_data = df_restaurant_processed.iloc[start_idx:end_idx]

            shard_pbar.set_description(f"Shard {shard_id+1}/{num_shards} ({len(shard_data)} records)")

            try:
                documents = create_documents_from_dataframe(shard_data)

                if len(documents) == 0:
                    print(f"⚠️ Shard {shard_id} has no valid documents, skipping...")
                    failed_shards += 1
                    shard_pbar.update(1)
                    continue

                collection_name = f"food_shard_{shard_id}"
                persist_directory = base_dir

                print(f"💾 Creating vectorstore for shard {shard_id} with {len(documents)} documents...")

                # Create persistent client
                persistent_client = chromadb.PersistentClient(path=persist_directory)

                vectorstore = Chroma(
                    client=persistent_client,
                    collection_name=collection_name,
                    embedding_function=embeddings,
                    persist_directory=persist_directory,
                    collection_metadata={"hnsw:space": "cosine"}
                )

                # Add documents in smaller batches to avoid memory issues
                batch_size = 4096  # Adjust batch size based on memory constraints
                for i in range(0, len(documents), batch_size):
                    batch = documents[i:i+batch_size]
                    vectorstore.add_documents(batch)

                # Verify storage
                collection = persistent_client.get_collection(collection_name)
                stored_count = collection.count()
                print(f"✅ Shard {shard_id} stored {stored_count} documents successfully")

                # Store shard info
                shard_info = f"{shard_id},{collection_name},{persist_directory},{stored_count},{start_idx},{end_idx}"
                shard_info_list.append(shard_info)
                successful_shards += 1

                # Clean up
                del vectorstore, persistent_client
                gc.collect()

            except Exception as e:
                print(f"❌ Shard {shard_id} failed: {str(e)}")
                failed_shards += 1

            shard_pbar.update(1)

    # Save shard info
    shard_info_path = os.path.join(data_dir, "shard_paths.txt")
    with open(shard_info_path, 'w') as f:
        f.write("shard_id,collection_name,persist_directory,document_count,start_idx,end_idx\n")
        for info in shard_info_list:
            f.write(info + "\n")

    print(f"\n🎯 **SUMMARY**")
    print(f"✅ Successful shards: {successful_shards}")
    print(f"❌ Failed shards: {failed_shards}")
    print(f"📄 Shard info saved to: {shard_info_path}")

    return shard_info_path


# Verify dataframe
required_columns = ['json_string_for_embedding', 'json_metadata']
missing_columns = [col for col in required_columns if col not in df_restaurant_processed.columns]

if missing_columns:
    print(f"❌ Missing required columns: {missing_columns}")
else:
    # Add DataFrame validation
    print(f"📊 DataFrame shape: {df_restaurant_processed.shape}")
    print(f"🔍 Sample data check:")
    print(f"  - json_string_for_embedding null count: {df_restaurant_processed['json_string_for_embedding'].isna().sum()}")
    print(f"  - json_metadata null count: {df_restaurant_processed['json_metadata'].isna().sum()}")

    available_memory_gb = psutil.virtual_memory().available / (1024**3)
    print(f"💾 Available memory: {available_memory_gb:.1f}GB")

    shard_size = 150000 # Single shard for 10k records if enough memory

    print(f"🎯 Using shard size: {shard_size}")

    shard_paths_file = create_multi_shard_chroma_store(
        df_restaurant_processed,
        embeddings,
        shard_size=shard_size
    )


📊 DataFrame shape: (1063888, 35)
🔍 Sample data check:
  - json_string_for_embedding null count: 0
  - json_metadata null count: 0
💾 Available memory: 8.0GB
🎯 Using shard size: 150000
🚀 Processing 1,063,888 records into 8 shards
📊 Shard size: 150,000 records per shard


Shard 1/8 (150000 records):   0%|          | 0/8 [00:00<?, ?shard/s]

📝 Processing 150000 records into documents...



Creating documents: 100%|██████████| 150000/150000 [00:26<00:00, 5714.25docs/s]


✅ Created 150000 documents, failed: 0
💾 Creating vectorstore for shard 0 with 150000 documents...
✅ Shard 0 stored 150000 documents successfully


...

📝 Processing 13888 records into documents...



Creating documents: 100%|██████████| 13888/13888 [00:02<00:00, 6861.79docs/s]


✅ Created 13888 documents, failed: 0
💾 Creating vectorstore for shard 7 with 13888 documents...
✅ Shard 7 stored 13888 documents successfully


Shard 8/8 (13888 records): 100%|██████████| 8/8 [37:41<00:00, 282.75s/shard]


🎯 **SUMMARY**
✅ Successful shards: 8
❌ Failed shards: 0
📄 Shard info saved to: ./shard_data/shard_paths.txt


In [ ]:
print(shard_paths_file)

gc.collect()
check_memory()

./shard_data/shard_paths.txt


True

In [ ]:
import shutil
from google.colab import files

# Replace 'folder_name' with your folder path
shutil.make_archive('chroma_shards', 'zip', 'chroma_shards')  # output will be folder_name.zip
files.download('chroma_shards.zip')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
    memory = psutil.virtual_memory()
    print(f"🖥️ RAM Status:")
    print(f"Total: {memory.total / (1024**3):.1f} GB")
    print(f"Available: {memory.available / (1024**3):.1f} GB")
    print(f"Used: {memory.percent:.1f}%")

🖥️ RAM Status:
Total: 12.7 GB
Available: 5.3 GB
Used: 58.0%


In [ ]:
x='''
Your goal is to structure the user's query to match the request schema provided below.

<< Structured Request Schema >>
When responding use a markdown code snippet with a JSON object formatted in the following schema:

```json
{
    "query": string,           // text string to compare with document contents
    "filter": object | "NO_FILTER" // a Chroma-compatible JSON filter or "NO_FILTER"
}
```

The query should only include keywords relevant to matching the content of documents. Filter conditions should only be included in the "filter" field and not repeated in the query.

<< Filter Format >>
The "filter" field should be a valid JSON object compatible with ChromaDB’s syntax for metadata filtering.

Supported Operators:
- Comparison: `$eq`, `$ne`, `$gt`, `$gte`, `$lt`, `$lte`, `$in`, `$nin`
- Logical: `$and`, `$or`, `$not`

Use only attribute names that exist in the data source and ensure all values are valid based on the attribute types and descriptions.

If no filters are necessary, return `"filter": "NO_FILTER"`.


Data Source:
```json
{
    "content": "Food items with detailed information about cuisine, dietary preferences, pricing, popularity, and availability",
    "attributes": {
        "food": {
            "description": "Name of the food item (e.g., burger, pizza, pasta)",
            "type": "string"
        },
        "cuisine_1": {
            "description": "Type of cuisine 'beverages','fast food', 'sweets', 'italianamerican', 'continental', 'north indian', 'snacks', 'indian', 'juices', 'tandoor', 'punjabi', 'mughlai', 'pizzas', 'chinese', 'ice cream', 'chaat', 'bakery', 'american', 'european', 'biryani', 'south indian', 'desserts', 'street food', 'nepalese', 'paan', 'healthy food', 'bengali', 'thalis', 'waffle', 'arabian', 'combo', 'tibetan', 'bihari', 'italian', 'salads', 'kebabs', 'asian', 'thai', 'north eastern', 'cafe', 'pan-asian', 'lebanese', 'maharashtrian', 'mexican', 'pastas', 'rajasthani', 'gujarati', 'seafood', 'japanese', 'sushi', 'middle eastern', 'french', 'hyderabadi', 'grill', 'svanidhi street food vendor', 'afghani', 'oriental', 'home food', 'barbecue', 'korean', 'kerala', 'andhra', 'british', 'oriya', 'portuguese', 'lucknowi', 'mangalorean', 'chettinad', 'mediterranean', 'naga', 'turkish', 'assamese', 'steakhouse', 'coastal', 'tex-mex'",
            "type": "string"
        },
        "cuisine_2": {
            "description": "Type of cuisine  'pizzas', 'bakery','fast food', 'indian', 'chaat', 'beverages', 'desserts', 'chinese', 'north indian', 'tandoor', 'american', 'thalis', 'snacks', 'south indian', 'italian', 'street food', 'kebabs', 'biryani', 'salads', 'pastas', 'continental', 'bengali', , 'ice cream', 'tibetan', 'thai', 'hyderabadi', 'sweets', 'lebanese', 'nepalese', 'mughlai', 'lucknowi', 'healthy food', 'afghani', 'asian', 'combo', 'seafood', 'waffle', 'italianamerican', 'punjabi', 'arabian', 'barbecue', 'mexican', 'ice cream cakes', 'gujarati', 'juices', 'jain', 'pan-asian', 'rajasthani', 'mediterranean', 'burmese', 'oriental', 'maharashtrian', 'kerala', 'home food', 'indonesian', 'middle eastern', 'grill', 'japanese', 'paan', 'biryani - shivaji military hotel', 'greek', 'cafe', 'use code jumbo30 to avail', 'chettinad', 'coastal', 'andhra', 'turkish', 'african', 'tex-mex', 'oriya', 'british', 'mangalorean', 'bihari', 'keto', 'european', 'malaysian', 'north eastern'",
            "type": "string"
        },
        "dietary": {
            "description": " Dietary preference: 'veg' or 'nonveg' or 'vegan' ",
            "type": "string"
        },
        "price_tier": {
            "description": "Price tier: within the budget use 'budget', not under  budget use 'affordable',and other are  'premium', or 'luxury'",
            "type": "string"
        },
        "popularity": {
            "description": "Popularity level: if its recently getting famous use 'emerging',already popular use 'popular', or 'very_popular' accordingly",
            "type": "string"
        },
        "label": {
            "description": "Special labels like 'bestseller', 'must try', 'chef's special', 'new', 'seasonal', 'spicy', 'fodmap friendly','eggless available', 'gluten free', 'dairy free",
            "type": "string"
        },
        "location": {
            "description": "City or location where the restaurant and food is available 'abohar', 'adilabad', 'adityapur', 'adoni', 'agartala', 'agra', 'vastrapur,ahmedabad', 'gota,ahmedabad', 'paldi & ambawadi,ahmedabad', 'ghatlodia,ahmedabad', 'bopal,ahmedabad', 'gandhinagar,ahmedabad', 'laldarwaja,ahmedabad', 'naranpura,ahmedabad', 'navrangpura,ahmedabad', 'science city,ahmedabad', 'maninagar,ahmedabad', 'chandkheda,ahmedabad', 'ahmednagar', 'aizawl', 'ajmer', 'akola', 'alappuzha', 'aligarh', 'alipurduar', 'allahabad', 'alwar', 'ambala', 'ambikapur', 'ambur', 'amravati', 'amreli', 'amritsar', 'anand', 'anantapur', 'ankleshwar', 'arakkonam', 'arambagh', 'arrah', 'aruppukottai', 'asansol', 'aurangabad', 'aurangabad_bihar', 'azamgarh', 'baddi', 'bagalkot', 'bagdogra', 'bahadurgarh', 'bahraich', 'balaghat', 'balangir', 'balasore', 'ballari', 'balrampur', 'balurghat', 'banda', 'yeshwanthpur,bangalore', 'geddalahalli,bangalore', 'koramangala,bangalore', 'jp nagar,bangalore', 'mahadevpura,bangalore', 'hsr,bangalore'",
            "type": "string"
        },
        "restaurant": {
            "description": "Name of the restaurant serving the food",
            "type": "string"
        },
        "f_id": {
            "description": "Unique identifier for the food item",
            "type": "string"
        },
        "r_id": {
            "description": "Unique identifier for the restaurant",
            "type": "string"
        },
        "f_price": {
            "description": "Price of the food item in INR, used for tiering",
            "type": "integer"
        },
        "f_rating": {
            "description": "Rating of the food item out of 5",
            "type": "float"
        },
        "r_rating": {
            "description": "Rating of the restaurant out of 5",
            "type": "float"
        }

    }
}
```

<< Example 1. >>
User Query: Show me bestseller pizza or italian food

Structured Request:
```json
{
    "query": "pizza italian food",
    "filter": {
        "$and": [
            { "label": { "$eq": "bestseller" } },
            {
                "$or": [
                    { "cuisine_1": { "$eq": "pizzas" } },
                    { "cuisine_2": { "$eq": "pizzas" } },
                    { "cuisine_1": { "$eq": "italian" } },
                    { "cuisine_2": { "$eq": "italian" } }
                ]
            }
        ]
    }
}
```

<< Example 2. >>
User Query: Find popular north indian tandoor dishes

Structured Request:
```json
{
    "query": "tandoor dishes",
    "filter": {
        "$and": [
            { "popularity": { "$eq": "popular" } },
            {
                "$or": [
                    { "cuisine_1": { "$eq": "north indian" } },
                    { "cuisine_2": { "$eq": "north indian" } },
                    { "cuisine_1": { "$eq": "tandoor" } },
                    { "cuisine_2": { "$eq": "tandoor" } }
                ]
            }
        ]
    }
}
```


<< Example 3. >>
User Query: I want vegetarian chinese food under budget in bangalore

Structured Request:
```json
{
    "query": "chinese food",
    "filter": {
        "$and": [
            { "veg_or_non_veg": { "$eq": "veg" } },
            {
                "$or": [
                    { "cuisine_1": { "$eq": "chinese" } },
                    { "cuisine_2": { "$eq": "chinese" } }
                ]
            },
            { "price": { "$eq": "budget" } },
            { "location":  { "$in": ["yeshwanthpur,bangalore", "geddalahalli,bangalore", "koramangala,bangalore", "jp nagar,bangalore", "mahadevpura,bangalore", "hsr,bangalore"] } }
        ]
    }
}
```


User Query:

Structured Request:


If no filtering is applicable for a user query, return `"filter": "NO_FILTER"` and a suitable `"query"` string.
'''

In [ ]:
sample_embedding = embeddings.embed_query("test")
print(f"Embedding dimension: {len(sample_embedding)}")

Embedding dimension: 384


In [ ]:
import pandas as pd

# Read the CSV listing your shards
shard_info_path = "./shard_data/shard_paths.txt"
shards_df = pd.read_csv(shard_info_path)
shards_df


shard_id collection_name persist_directory  document_count  start_idx  \
0         0    food_shard_0   ./chroma_shards          150000          0   
1         1    food_shard_1   ./chroma_shards          150000     150000   
2         2    food_shard_2   ./chroma_shards          150000     300000   
3         3    food_shard_3   ./chroma_shards          150000     450000   
4         4    food_shard_4   ./chroma_shards          150000     600000   
5         5    food_shard_5   ./chroma_shards          150000     750000   
6         6    food_shard_6   ./chroma_shards          150000     900000   
7         7    food_shard_7   ./chroma_shards           13888    1050000   

   end_idx  
0   150000  
1   300000  
2   450000  
3   600000  
4   750000  
5   900000  
6  1050000  
7  1063888

In [ ]:
# user_query = input("Enter your search query: ")

In [ ]:
def setup_embeddings_cpu():
    available_memory_gb = psutil.virtual_memory().available / (1024**3)
    model_name = "sentence-transformers/all-MiniLM-L6-v2"

    embeddings = HuggingFaceEmbeddings(
        model_name=model_name,
        model_kwargs={'device': 'cpu'},
        encode_kwargs={'normalize_embeddings': True}
    )

    return embeddings

    # Setup embeddings
embeddings1 = setup_embeddings_cpu()

In [ ]:
print(df_restaurant_processed["f_name"].unique().tolist())

['aloo tikki burger', 'veg creamy burger', 'cheese burst burger', 'paneer creamy burger', 'maxican burger', 'bbq chicken burger', 'peri peri chicken burger', 'white sauce', 'red sauce', 'pink sauce', 'masala pasta', 'chicken pasta', 'egg pasta', 'noodles', 'singapuri noodles', 'hakka noodles', 'garlic noodles', 'paneer noodles', 'dry manchurian', 'gravy manchurian', 'cheese chilly dry', 'cheese chilly gravy', 'egg chilly', 'chicken chilly', 'spring roll 2pc', 'momos 8pc', 'honey chilly patato', 'honey chilly cauliflower', 'veg fried rice', 'chicken fried rice', 'kfc fried chicken', 'fried chicken', 'veg mayo sandwich', 'veg creamy sandwich', 'bombay sandwich', 'paneer tikka sandwich', 'chicken sandwich', 'peri peri sandwich', 'egg sandwich', 'classical fries', 'red chilli papper', 'creamy fries', 'peri peri fries', 'egg roll', 'veg roll', 'paneer roll', 'chicken roll', 'egg chicken roll double', 'veg wrapes', 'paneer wrapes', 'peri peri chicken wrapes', 'egg wrapes', 'simple garlic bre

In [ ]:
user_query= "american chese burger under 400rsand rating above 4 and  restaurant rating above 3.5"

In [ ]:
embedded_query1 = embeddings1.embed_query(user_query)
print(embedded_query1)

[0.03977499157190323, -0.0329652838408947, -0.03328932449221611, -0.003279999131336808, -0.046556051820516586, 0.006495509762316942, 0.008681325241923332, 0.08389857411384583, 0.0343606099486351, -0.042007021605968475, 0.00304295658133924, -0.014465979300439358, 0.038227904587984085, -0.09210093319416046, -0.03380601480603218, -0.11989828944206238, 0.16543106734752655, -0.06043320149183273, -0.06640776246786118, -0.06980371475219727, 0.012255838140845299, -0.06461143493652344, 0.11301244795322418, 0.06187319755554199, -0.043320432305336, -0.08846473693847656, 0.005395364481955767, 0.02561020664870739, -0.07240990549325943, -0.022853538393974304, 0.02905220352113247, -0.09089348465204239, -0.010090994648635387, -0.041248247027397156, 0.03653113543987274, -0.031052375212311745, 0.05991731584072113, -0.08150066435337067, -0.02392606995999813, 0.041973408311605453, -0.005782923195511103, -0.007543966639786959, -0.020004525780677795, -0.02705499716103077, 0.06947148591279984, 0.057743810117

In [ ]:
embedded_query = embeddings.embed_query(user_query)
print(embedded_query)

[0.03977498039603233, -0.03296525776386261, -0.03328929468989372, -0.0032800135668367147, -0.04655605927109718, 0.006495499052107334, 0.008681328035891056, 0.08389855921268463, 0.034360598772764206, -0.04200701043009758, 0.003042982891201973, -0.014465993270277977, 0.03822790086269379, -0.09210095554590225, -0.03380599617958069, -0.11989831179380417, 0.16543108224868774, -0.06043320521712303, -0.06640775501728058, -0.06980369985103607, 0.01225585862994194, -0.06461140513420105, 0.11301243305206299, 0.06187320128083229, -0.04332045838236809, -0.08846469968557358, 0.0053954278118908405, 0.0256101805716753, -0.07240989059209824, -0.022853510454297066, 0.02905220165848732, -0.09089347720146179, -0.010090983472764492, -0.04124826565384865, 0.036531101912260056, -0.031052319332957268, 0.0599173940718174, -0.08150069415569305, -0.023926114663481712, 0.04197336733341217, -0.0057829152792692184, -0.007543973159044981, -0.0200045108795166, -0.02705501765012741, 0.06947152316570282, 0.05774378404

In [ ]:
# Calculate cosine similarity
cosine_sim = np.dot(embedded_query1, embedded_query) / (np.linalg.norm(embedded_query1) * np.linalg.norm(embedded_query))
print(f"Cosine similarity: {cosine_sim:.10f}")

Cosine similarity: 1.0000000000


In [ ]:
import json
import os
import re
import openai


class CustomSelfQueryConstructor:
    def __init__(self, prompt_template):
        self.prompt_template = prompt_template
        openai.api_key = os.environ["OPENAI_API_KEY"]

    def query(self, user_query):
        print("Sending request to OpenAI GPT-4o...")
        response = openai.chat.completions.create(
            model="gpt-4o-mini",
            messages=[{
                "role": "user",
                "content": f"{self.prompt_template}\n\nUser Query:\n{user_query}\n\nStructured Request:"
            }]
        )

        content = response.choices[0].message.content
        print("Raw LLM Response:")
        print(content)
        print("=" * 50)

        match = re.search(r"```(?:json)?\n(.*?)```", content, re.DOTALL)
        if not match:
            raise ValueError("No JSON code block found in LLM response")

        json_str = match.group(1)
        data = json.loads(json_str)

        query = data["query"]
        chroma_filter = data.get("filter")

        print(f"Parsed Query: {query}")
        print(f"ChromaDB Filter: {json.dumps(chroma_filter, indent=2)}")
        print("=" * 50)

        return query, chroma_filter


# Usage
retriever = CustomSelfQueryConstructor(
    prompt_template=x  # replace x with your actual prompt template string
)

query, chroma_filter = retriever.query(user_query)
print(f"Query: {query}")
print(f"Chroma Filter: {chroma_filter}")


Sending request to OpenAI GPT-4o...
Raw LLM Response:
```json
{
    "query": "american cheese burger",
    "filter": {
        "$and": [
            { "f_price": { "$lte": 400 } },
            { "f_rating": { "$gt": 4 } },
            { "r_rating": { "$gt": 3.5 } }
        ]
    }
}
```
Parsed Query: american cheese burger
ChromaDB Filter: {
  "$and": [
    {
      "f_price": {
        "$lte": 400
      }
    },
    {
      "f_rating": {
        "$gt": 4
      }
    },
    {
      "r_rating": {
        "$gt": 3.5
      }
    }
  ]
}
Query: american cheese burger
Chroma Filter: {'$and': [{'f_price': {'$lte': 400}}, {'f_rating': {'$gt': 4}}, {'r_rating': {'$gt': 3.5}}]}


In [ ]:
query = "american cheese burger"
chroma_filter = {'$and': [{'f_price': {'$lte': 400}}, {'f_rating': {'$gt': 4}}, {'r_rating': {'$gt': 3.5}}]}

In [ ]:
shards_df

shard_id collection_name persist_directory  document_count  start_idx  \
0         0    food_shard_0   ./chroma_shards          150000          0   
1         1    food_shard_1   ./chroma_shards          150000     150000   
2         2    food_shard_2   ./chroma_shards          150000     300000   
3         3    food_shard_3   ./chroma_shards          150000     450000   
4         4    food_shard_4   ./chroma_shards          150000     600000   
5         5    food_shard_5   ./chroma_shards          150000     750000   
6         6    food_shard_6   ./chroma_shards          150000     900000   
7         7    food_shard_7   ./chroma_shards           13888    1050000   

   end_idx  
0   150000  
1   300000  
2   450000  
3   600000  
4   750000  
5   900000  
6  1050000  
7  1063888

In [ ]:
import asyncio
from langchain_chroma import Chroma


def search_shard(shard_meta, query, chroma_filter, top_k=5):
    # Load each Chroma collection
    collection_path = shard_meta['persist_directory']
    # Ensure the path exists
    if not os.path.exists(collection_path):
        raise FileNotFoundError(f"Collection path does not exist: {collection_path}")

    # Important: Use the same embedding method/initialization as when you created the shards!
    vectordb = Chroma(
        persist_directory=collection_path,
        collection_name=shard_meta['collection_name'],
        embedding_function=embeddings1,  # Initialize as in your notebook
    )
    # Similarity search with filter
    results = vectordb.similarity_search_with_relevance_scores(
        query=query,
        k=top_k,
        filter=None if chroma_filter == "NO_FILTER" else chroma_filter  # Structured filter for Chroma
    )
    return results

async def gather_shard_results(shards_df, query, chroma_filter, top_k=5):
    loop = asyncio.get_event_loop()
    tasks = []
    # Use ThreadPoolExecutor so Chroma & file I/O don't block asyncio
    with ThreadPoolExecutor(max_workers=min(32, len(shards_df))) as executor:
        for idx, shard_meta in shards_df.iterrows():
            task = loop.run_in_executor(
                executor,
                search_shard,
                shard_meta,
                query,
                chroma_filter,
                top_k
            )
            tasks.append(task)
        all_results = await asyncio.gather(*tasks)
    # Flatten results
    return all_results


In [ ]:
top_k_per_shard = 5
all_shard_docs = await gather_shard_results(shards_df, query, chroma_filter, top_k=top_k_per_shard)
print(f"Total docs gathered from all shards: {len(all_shard_docs)}")





Total docs gathered from all shards: 8


In [ ]:
data = []
for doc in all_shard_docs:
    for d,s in doc:
        data.append(
            {
                "doc": d,
                "score": s
            }
        )

data




[{'doc': Document(id='f01e9006-0a77-4738-9094-ce46b5563c1e', metadata={'f_id': 'fd327', 'food': 'american cheese burger', 'popularity': 'very_popular', 'cuisine_1': 'beverages', 'r_rating': 3.8, 'f_rating': 4.3, 'f_price': 220, 'cuisine_2': 'nan', 'label': 'bestseller', 'location': 'abohar', 'restaurant': 'theka coffee desi', 'dietary': 'veg', 'price_tier': 'affordable', 'r_id': '158203.0'}, page_content="food name is 'american cheese burger', comes under 'beverages and nan cuisine' dish, it's dietary: veg "),
  'score': 0.6468639969825745},
 {'doc': Document(id='154746a3-7507-4ae2-9632-b4949fd3bf4b', metadata={'label': 'must try', 'dietary': 'veg', 'location': 'vastrapur,ahmedabad', 'f_rating': 4.1, 'f_id': 'fd148794', 'r_rating': 4.1, 'food': 'triple cheese american burger veg', 'price_tier': 'premium', 'cuisine_1': 'burgers', 'r_id': '395181.0', 'restaurant': 'mcdonalds gourmet burger collection', 'f_price': 179, 'popularity': 'very_popular', 'cuisine_2': 'beverages'}, page_content=

In [ ]:
sorted_data = sorted(data, key=lambda x: x['score'], reverse=True)
top_results = sorted_data[:10]  # Get top 10 results
top_results

[{'doc': Document(id='2a351e98-69cb-46ae-ba81-48934226fbb1', metadata={'label': 'bestseller', 'r_id': '64131.0', 'cuisine_2': 'continental', 'location': 'jp nagar,bangalore', 'popularity': 'very_popular', 'f_id': 'fd36407', 'dietary': 'veg', 'price_tier': 'affordable', 'cuisine_1': 'american', 'r_rating': 4.4, 'restaurant': 'truffles', 'f_price': 199, 'food': 'cottage cheese burger', 'f_rating': 4.7}, page_content="food name is 'cottage cheese burger', comes under 'american and continental cuisine' dish, it's dietary: veg "),
  'score': 0.6487430334091187},
 {'doc': Document(id='8cf248e0-4026-49d5-b69b-170b97c5f31d', metadata={'dietary': 'nonveg', 'cuisine_2': 'continental', 'food': 'double cheese burger', 'cuisine_1': 'american', 'r_id': '540918.0', 'price_tier': 'luxury', 'f_id': 'fd596989', 'r_rating': 4.2, 'location': 'jp nagar,bangalore', 'f_rating': 4.3, 'f_price': 225, 'label': 'bestseller', 'restaurant': 'steak queen', 'popularity': 'very_popular'}, page_content="food name is '